# Machine Learning Foundation

## Course 5, Part i: Reinforcement Learning DEMO

## Reinforcement Learning Example

In this example from Reinforcement Learning, the task is to use tools from Machine Learning to predict how an agent should act. We will then use those predictions to drive the behavior of the agent. Ideally, our intelligent agent should get a much better score than a random agent.

## Key concepts:

- **Observation**: These are the states of the game. It describes where the agent currently is.
- **Action**: These are the moves that the agent makes.
- **Episode**: One full game played from beginning (`env.reset()`) to end (when `done == True`).
- **Step**: Part of a game that includes one action. The game transitions from one observation to the next.

## Setup

This exaple uses the Python library [OpenAI Gym](https://gym.openai.com/docs/).

If you want to install everything (gym can run atari games.) follow [these instructions](https://github.com/openai/gym#installing-everything).

Now we can build an environment using OpenAI. 

In [1]:
import gym
import pandas
import numpy as np

# The first part of the game uses the environment FrozenLake-V0

This is a small world with 16 tiles. 

    SFFF
    FHFH
    FFFH
    HFFG

The game starts at the S tile. The object of the game is to get to the goal (G) without landing in a hole (H).

In [2]:
# Build an environment with gym.make()
env = gym.make('FrozenLake-v0') # build a fresh environment

# Start a new game with env.reset()
current_observation = env.reset() # this starts a new "episode" and returns the initial observation

#the current observation is just the current location
print(current_observation) # observations are just a number

0


In [3]:
# we can print the environment if we want to look at it
env.render() 


SFFF
FHFH
FFFH
HFFG


In [4]:
# the action space for this environment includes four discrete actions

print(f"our action space: {env.action_space}")

new_action = env.action_space.sample() # we can randomly sample actions

print(f"our new action: {new_action}") # run this cell a few times to get an idea of the action space
# what does it look like?

our action space: Discrete(4)
our new action: 1


In [5]:
# now we act! do this with the step function

new_action = env.action_space.sample()

observation, reward, done, info = env.step(new_action)

# here's a look at what we get back
print(f"observation: {observation}, reward: {reward}, done: {done}, info: {info}")

env.render() 

observation: 1, reward: 0.0, done: False, info: {'prob': 0.3333333333333333}
  (Up)
SFFF
FHFH
FFFH
HFFG


In [6]:
# we can put this process into a for-loop and see how the game progresses

current_observation = env.reset() # start a new game

for i in range(5): # run 5 moves

    new_action = env.action_space.sample() # same a new action

    observation, reward, done, info = env.step(new_action) # step through the action and get the outputs

    # here's a look at what we get back
    print(f"observation: {observation}, reward: {reward}, done: {done}, info: {info}")

    env.render() 

observation: 0, reward: 0.0, done: False, info: {'prob': 0.3333333333333333}
  (Left)
SFFF
FHFH
FFFH
HFFG
observation: 4, reward: 0.0, done: False, info: {'prob': 0.3333333333333333}
  (Down)
SFFF
FHFH
FFFH
HFFG
observation: 4, reward: 0.0, done: False, info: {'prob': 0.3333333333333333}
  (Left)
SFFF
FHFH
FFFH
HFFG
observation: 4, reward: 0.0, done: False, info: {'prob': 0.3333333333333333}
  (Down)
SFFF
FHFH
FFFH
HFFG
observation: 5, reward: 0.0, done: True, info: {'prob': 0.3333333333333333}
  (Down)
SFFF
FHFH
FFFH
HFFG


Now we can guess what each of the outputs mean. 

**Observation** refers to the number of the tile. The tiles appear to be numbered

    0 1 2 3
    4 5 ...
    
**Reward** refers to the outcome of the game. We get 1 if we win, zero otherwise.

**Done** tells us if the game is still going. It goes to true when we win or fall into a hole.

**info** gives extra info about the world. Here, it's probabilities. Can you guess what this means here? Perhaps the world is a bit noisy.

In [7]:
# Here's how to simulate an entire episode
# We're going to stop rendering it every time to save space
# try running this a few. Does it ever win?

current_observation = env.reset()
done = False

while not done:   
    print("Before action: ")
    env.render()
    new_action = env.action_space.sample()
    new_observation, reward, done, info = env.step(new_action)
#     print(f"action:{new_action} observation: {new_observation}, reward: {reward}, done: {done}, info: {info}")
    print("After action: ")
    env.render()

Before action: 

SFFF
FHFH
FFFH
HFFG
After action: 
  (Down)
SFFF
FHFH
FFFH
HFFG
Before action: 
  (Down)
SFFF
FHFH
FFFH
HFFG
After action: 
  (Right)
SFFF
FHFH
FFFH
HFFG
Before action: 
  (Right)
SFFF
FHFH
FFFH
HFFG
After action: 
  (Left)
SFFF
FHFH
FFFH
HFFG
Before action: 
  (Left)
SFFF
FHFH
FFFH
HFFG
After action: 
  (Left)
SFFF
FHFH
FFFH
HFFG
Before action: 
  (Left)
SFFF
FHFH
FFFH
HFFG
After action: 
  (Left)
SFFF
FHFH
FFFH
HFFG
Before action: 
  (Left)
SFFF
FHFH
FFFH
HFFG
After action: 
  (Down)
SFFF
FHFH
FFFH
HFFG


Things to think about:
- What things do you notice about how the environment and actions work?
- What do you think the actions mean?
- When the agent performs the same action from the same place (same observation), does the same outcome happen every time?

The environment has some squares that always end the game (`H` in the render), some that don't (`F`), and one that is presumably the reward, if you get to it.

The actions seem like up, down, left right. But they also seem stochastic. There seems to be a 1/3 chance of going into 3 different squares with each action. 

# Part 1: Gather data

We want to build an intelligent actor but first we have to gather data on which actions are useful.

Use the above code as reference. Run a *random* agent through 1,000 or more episodes and collect data on each step.

I recommend you store this data in a pandas dataframe. Each row should be a step. Your features should include the following features or similar 

- `observation` the observation at the beginning of the step (before acting!)
- `action` the action randomly sampled
- `current_reward` the reward received after the action was performed

After you generate this data, it is recommended that you compute a column (e.g. `total_reward` that is the total reward for the entire episode).

At the end of the data gathering, you should be able to use pandas (or similar) to calculate the average total reward *per episode* of the random agent. The average score should be 1-2%, meaning that the agent very rarely wins.


## Hints

- `initial_observation = env.reset()` starts a new episode and returns the initial observation.
- `new_observation, reward, done, info = env.step(new_action)` executes one action and returns the following observation. You may look at the documentation for the step method if you are curious about what it does. 
- `done != True` until the game is finished.
- we are trying to maximize the reward *per episode*. Our first game gives 0 reward unless the agent travels to the goal.
- `env.action_space.n` gives the number of possible actions in the environment. `env.action_space.sample()` allows the agent to randomly sample an action.
- `env.observation_space.n` gives the number of possible states in the environment. 

In [8]:
env = gym.make('FrozenLake-v0')

num_episodes = 40000

life_memory = []
for i in range(num_episodes):
    
    # start a new episode and record all the memories
    old_observation = env.reset()
    done = False
    tot_reward = 0
    ep_memory = []
    while not done:
        new_action = env.action_space.sample()
        observation, reward, done, info = env.step(new_action)
        tot_reward += reward
        
        ep_memory.append({
            "observation": old_observation,
            "action": new_action,
            "reward": reward,
            "episode": i,
        })
        old_observation = observation
        
    # incorporate total reward
    num_steps = len(ep_memory)
    for i, ep_mem in enumerate(ep_memory):
        ep_mem["tot_reward"] = tot_reward
        ep_mem["decay_reward"] = i*tot_reward/num_steps
        
    life_memory.extend(ep_memory)
    
memory_df = pandas.DataFrame(life_memory)

In [9]:
memory_df

observation  action  reward  episode  tot_reward  decay_reward
0                 0       3     0.0        0         0.0           0.0
1                 0       2     0.0        0         0.0           0.0
2                 4       1     0.0        0         0.0           0.0
3                 0       0     0.0        1         0.0           0.0
4                 0       3     0.0        1         0.0           0.0
...             ...     ...     ...      ...         ...           ...
305750            4       1     0.0    39998         0.0           0.0
305751            8       1     0.0    39998         0.0           0.0
305752            0       0     0.0    39999         0.0           0.0
305753            4       1     0.0    39999         0.0           0.0
305754            4       3     0.0    39999         0.0           0.0

[305755 rows x 6 columns]

In [10]:
for i, ep_mem in enumerate(ep_memory):
    print(i, ep_mem)

0 {'observation': 0, 'action': 0, 'reward': 0.0, 'episode': 39999, 'tot_reward': 0.0, 'decay_reward': 0.0}
1 {'observation': 4, 'action': 1, 'reward': 0.0, 'episode': 39999, 'tot_reward': 0.0, 'decay_reward': 0.0}
2 {'observation': 4, 'action': 3, 'reward': 0.0, 'episode': 39999, 'tot_reward': 0.0, 'decay_reward': 0.0}


In [11]:
memory_df.describe()

observation         action         reward        episode  \
count  305755.000000  305755.000000  305755.000000  305755.000000   
mean        2.248657       1.497470       0.001887   19996.755873   
std         3.014509       1.117792       0.043400   11557.155704   
min         0.000000       0.000000       0.000000       0.000000   
25%         0.000000       0.000000       0.000000    9964.000000   
50%         1.000000       1.000000       0.000000   20052.000000   
75%         4.000000       2.000000       0.000000   30014.000000   
max        14.000000       3.000000       1.000000   39999.000000   

          tot_reward   decay_reward  
count  305755.000000  305755.000000  
mean        0.024265       0.011189  
std         0.153870       0.083954  
min         0.000000       0.000000  
25%         0.000000       0.000000  
50%         0.000000       0.000000  
75%         0.000000       0.000000  
max         1.000000       0.979592

In [12]:
memory_df.shape

(305755, 6)

In [ ]:
memory_df.groupby("episode").apply(display)

obs0      obs1      obs2      obs3  action  reward  episode  \
0   0.007139  0.018253  0.020815 -0.044640       0     1.0        0   
1   0.007504 -0.177161  0.019922  0.254537       0     1.0        0   
2   0.003961 -0.372562  0.025013  0.553436       1     1.0        0   
3  -0.003490 -0.177800  0.036082  0.268738       1     1.0        0   
4  -0.007046  0.016789  0.041457 -0.012350       0     1.0        0   
5  -0.006710 -0.178902  0.041210  0.293120       1     1.0        0   
6  -0.010288  0.015608  0.047072  0.013713       0     1.0        0   
7  -0.009976 -0.180156  0.047346  0.320868       1     1.0        0   
8  -0.013579  0.014261  0.053764  0.043484       1     1.0        0   
9  -0.013294  0.208572  0.054633 -0.231763       1     1.0        0   
10 -0.009123  0.402873  0.049998 -0.506724       1     1.0        0   
11 -0.001065  0.597256  0.039864 -0.783241       0     1.0        0   
12  0.010880  0.401609  0.024199 -0.478288       1     1.0        0   
13  0.018912  0.596382  0.014633 -0.763247       1     1.0        0   
14  0.030840  0.791299 -0.000632 -1.051290       1     1.0        0   
15  0.046666  0.986429 -0.021658 -1.344171       1     1.0        0   
16  0.066394  1.181817 -0.048541 -1.643550       0     1.0        0   
17  0.090031  0.987296 -0.081412 -1.366378       1     1.0        0   
18  0.109776  1.183337 -0.108740 -1.683374       0     1.0        0   
19  0.133443  0.989629 -0.142407 -1.426435       1     1.0        0   
20  0.153236  1.186194 -0.170936 -1.760025       1     1.0        0   
21  0.176960  1.382790 -0.206136 -2.100632       1     1.0        0   

    tot_reward  comb_reward  
0         22.0         22.5  
1         22.0         22.5  
2         22.0         22.5  
3         22.0         22.5  
4         22.0         22.5  
5         22.0         22.5  
6         22.0         22.5  
7         22.0         22.5  
8         22.0         22.5  
9         22.0         22.5  
10        22.0         22.5  
11        22.0         22.5  
12        22.0         22.5  
13        22.0         22.5  
14        22.0         22.5  
15        22.0         22.5  
16        22.0         22.5  
17        22.0         22.5  
18        22.0         22.5  
19        22.0         22.5  
20        22.0         22.5  
21        22.0         22.5

obs0      obs1      obs2      obs3  action  reward  episode  \
22 -0.043873  0.033733 -0.037173  0.001749       1     1.0        1   
23 -0.043199  0.229367 -0.037138 -0.302427       1     1.0        1   
24 -0.038611  0.424998 -0.043186 -0.606587       1     1.0        1   
25 -0.030111  0.620697 -0.055318 -0.912553       1     1.0        1   
26 -0.017698  0.816522 -0.073569 -1.222097       0     1.0        1   
27 -0.001367  0.622421 -0.098011 -0.953342       1     1.0        1   
28  0.011081  0.818715 -0.117078 -1.275140       0     1.0        1   
29  0.027456  0.625265 -0.142580 -1.021293       0     1.0        1   
30  0.039961  0.432300 -0.163006 -0.776561       1     1.0        1   
31  0.048607  0.629244 -0.178538 -1.115772       1     1.0        1   
32  0.061192  0.826202 -0.200853 -1.458724       1     1.0        1   

    tot_reward  comb_reward  
22        11.0         11.5  
23        11.0         11.5  
24        11.0         11.5  
25        11.0         11.5  
26        11.0         11.5  
27        11.0         11.5  
28        11.0         11.5  
29        11.0         11.5  
30        11.0         11.5  
31        11.0         11.5  
32        11.0         11.5

obs0      obs1      obs2      obs3  action  reward  episode  \
33 -0.048907  0.001241  0.035291 -0.003438       0     1.0        2   
34 -0.048882 -0.194369  0.035223  0.300167       0     1.0        2   
35 -0.052769 -0.389974  0.041226  0.603748       1     1.0        2   
36 -0.060569 -0.195453  0.053301  0.324330       1     1.0        2   
37 -0.064478 -0.001128  0.059788  0.048921       1     1.0        2   
38 -0.064501  0.193088  0.060766 -0.224316       1     1.0        2   
39 -0.060639  0.387291  0.056280 -0.497229       0     1.0        2   
40 -0.052893  0.191422  0.046335 -0.187354       0     1.0        2   
41 -0.049065 -0.004331  0.042588  0.119579       1     1.0        2   
42 -0.049151  0.190156  0.044980 -0.159370       1     1.0        2   
43 -0.045348  0.384606  0.041792 -0.437530       1     1.0        2   
44 -0.037656  0.579112  0.033042 -0.716752       1     1.0        2   
45 -0.026074  0.773762  0.018707 -0.998854       1     1.0        2   
46 -0.010598  0.968629 -0.001270 -1.285604       0     1.0        2   
47  0.008774  0.773523 -0.026983 -0.993319       1     1.0        2   
48  0.024245  0.968995 -0.046849 -1.294353       1     1.0        2   
49  0.043624  1.164680 -0.072736 -1.601326       1     1.0        2   
50  0.066918  1.360584 -0.104763 -1.915771       0     1.0        2   
51  0.094130  1.166734 -0.143078 -1.657334       1     1.0        2   
52  0.117464  1.363206 -0.176225 -1.990952       1     1.0        2   

    tot_reward  comb_reward  
33        20.0         20.5  
34        20.0         20.5  
35        20.0         20.5  
36        20.0         20.5  
37        20.0         20.5  
38        20.0         20.5  
39        20.0         20.5  
40        20.0         20.5  
41        20.0         20.5  
42        20.0         20.5  
43        20.0         20.5  
44        20.0         20.5  
45        20.0         20.5  
46        20.0         20.5  
47        20.0         20.5  
48        20.0         20.5  
49        20.0         20.5  
50        20.0         20.5  
51        20.0         20.5  
52        20.0         20.5

obs0      obs1      obs2      obs3  action  reward  episode  \
53 -0.010168  0.012337  0.006980  0.025288       1     1.0        3   
54 -0.009921  0.207358  0.007486 -0.265184       0     1.0        3   
55 -0.005774  0.012130  0.002182  0.029850       0     1.0        3   
56 -0.005531 -0.183023  0.002779  0.323221       1     1.0        3   
57 -0.009192  0.012060  0.009243  0.031416       1     1.0        3   
58 -0.008951  0.207048  0.009872 -0.258337       1     1.0        3   
59 -0.004810  0.402027  0.004705 -0.547890       0     1.0        3   
60  0.003231  0.206840 -0.006253 -0.253728       0     1.0        3   
61  0.007368  0.011808 -0.011327  0.036976       1     1.0        3   
62  0.007604  0.207090 -0.010588 -0.259259       0     1.0        3   
63  0.011746  0.012121 -0.015773  0.030065       0     1.0        3   
64  0.011988 -0.182771 -0.015172  0.317730       1     1.0        3   
65  0.008333  0.012563 -0.008817  0.020302       0     1.0        3   
66  0.008584 -0.182431 -0.008411  0.310190       0     1.0        3   
67  0.004935 -0.377432 -0.002207  0.600208       0     1.0        3   
68 -0.002613 -0.572523  0.009797  0.892195       1     1.0        3   
69 -0.014064 -0.377535  0.027641  0.602608       1     1.0        3   
70 -0.021615 -0.182811  0.039693  0.318757       0     1.0        3   
71 -0.025271 -0.378475  0.046068  0.623689       0     1.0        3   
72 -0.032840 -0.574209  0.058542  0.930518       0     1.0        3   
73 -0.044324 -0.770070  0.077152  1.241007       1     1.0        3   
74 -0.059726 -0.576019  0.101972  0.973456       0     1.0        3   
75 -0.071246 -0.772350  0.121441  1.296351       0     1.0        3   
76 -0.086693 -0.968787  0.147368  1.624453       1     1.0        3   
77 -0.106069 -0.775675  0.179857  1.381094       0     1.0        3   
78 -0.121582 -0.972527  0.207479  1.724203       1     1.0        3   

    tot_reward  comb_reward  
53        26.0         26.5  
54        26.0         26.5  
55        26.0         26.5  
56        26.0         26.5  
57        26.0         26.5  
58        26.0         26.5  
59        26.0         26.5  
60        26.0         26.5  
61        26.0         26.5  
62        26.0         26.5  
63        26.0         26.5  
64        26.0         26.5  
65        26.0         26.5  
66        26.0         26.5  
67        26.0         26.5  
68        26.0         26.5  
69        26.0         26.5  
70        26.0         26.5  
71        26.0         26.5  
72        26.0         26.5  
73        26.0         26.5  
74        26.0         26.5  
75        26.0         26.5  
76        26.0         26.5  
77        26.0         26.5  
78        26.0         26.5

obs0      obs1      obs2      obs3  action  reward  episode  \
79  0.031077 -0.028145 -0.044624 -0.005305       0     1.0        4   
80  0.030514 -0.222599 -0.044730  0.272971       1     1.0        4   
81  0.026062 -0.026868 -0.039271 -0.033477       1     1.0        4   
82  0.025525  0.168794 -0.039941 -0.338287       1     1.0        4   
83  0.028901  0.364461 -0.046706 -0.643293       1     1.0        4   
84  0.036190  0.560202 -0.059572 -0.950311       1     1.0        4   
85  0.047394  0.756073 -0.078578 -1.261100       0     1.0        4   
86  0.062515  0.562039 -0.103800 -0.994025       0     1.0        4   
87  0.073756  0.368447 -0.123681 -0.735663       0     1.0        4   
88  0.081125  0.175231 -0.138394 -0.484322       0     1.0        4   
89  0.084630 -0.017695 -0.148081 -0.238259       1     1.0        4   
90  0.084276  0.179198 -0.152846 -0.573743       0     1.0        4   
91  0.087860 -0.013488 -0.164321 -0.332846       1     1.0        4   
92  0.087590  0.183545 -0.170978 -0.672507       0     1.0        4   
93  0.091261 -0.008840 -0.184428 -0.438160       0     1.0        4   
94  0.091084 -0.200938 -0.193191 -0.208815       0     1.0        4   
95  0.087065 -0.392848 -0.197367  0.017250       1     1.0        4   
96  0.079208 -0.195524 -0.197022 -0.330640       1     1.0        4   
97  0.075298  0.001777 -0.203635 -0.678417       0     1.0        4   

    tot_reward  comb_reward  
79        19.0         19.5  
80        19.0         19.5  
81        19.0         19.5  
82        19.0         19.5  
83        19.0         19.5  
84        19.0         19.5  
85        19.0         19.5  
86        19.0         19.5  
87        19.0         19.5  
88        19.0         19.5  
89        19.0         19.5  
90        19.0         19.5  
91        19.0         19.5  
92        19.0         19.5  
93        19.0         19.5  
94        19.0         19.5  
95        19.0         19.5  
96        19.0         19.5  
97        19.0         19.5

...

obs0      obs1      obs2      obs3  action  reward  episode  \
15930  0.037528  0.005498 -0.032874 -0.021118       1     1.0      751   
15931  0.037638  0.201075 -0.033296 -0.323989       0     1.0      751   
15932  0.041660  0.006443 -0.039776 -0.041989       1     1.0      751   
15933  0.041789  0.202112 -0.040615 -0.346952       0     1.0      751   
15934  0.045831  0.007590 -0.047555 -0.067348       0     1.0      751   
15935  0.045983 -0.186819 -0.048901  0.209960       1     1.0      751   
15936  0.042246  0.008967 -0.044702 -0.097739       0     1.0      751   
15937  0.042426 -0.185487 -0.046657  0.180512       1     1.0      751   
15938  0.038716  0.010271 -0.043047 -0.126517       1     1.0      751   
15939  0.038921  0.205982 -0.045577 -0.432464       1     1.0      751   
15940  0.043041  0.401719 -0.054226 -0.739159       1     1.0      751   
15941  0.051075  0.597546 -0.069010 -1.048402       0     1.0      751   
15942  0.063026  0.403404 -0.089978 -0.778156       1     1.0      751   
15943  0.071095  0.599641 -0.105541 -1.097737       1     1.0      751   
15944  0.083087  0.795982 -0.127496 -1.421581       1     1.0      751   
15945  0.099007  0.992429 -0.155927 -1.751243       0     1.0      751   
15946  0.118856  0.799384 -0.190952 -1.510845       0     1.0      751   

       tot_reward  comb_reward  
15930        17.0         17.5  
15931        17.0         17.5  
15932        17.0         17.5  
15933        17.0         17.5  
15934        17.0         17.5  
15935        17.0         17.5  
15936        17.0         17.5  
15937        17.0         17.5  
15938        17.0         17.5  
15939        17.0         17.5  
15940        17.0         17.5  
15941        17.0         17.5  
15942        17.0         17.5  
15943        17.0         17.5  
15944        17.0         17.5  
15945        17.0         17.5  
15946        17.0         17.5

obs0      obs1      obs2      obs3  action  reward  episode  \
15947  0.002795  0.046764 -0.030538 -0.005027       1     1.0      752   
15948  0.003730  0.242310 -0.030639 -0.307187       1     1.0      752   
15949  0.008577  0.437855 -0.036783 -0.609373       1     1.0      752   
15950  0.017334  0.633471 -0.048970 -0.913410       0     1.0      752   
15951  0.030003  0.439045 -0.067238 -0.636512       0     1.0      752   
15952  0.038784  0.244922 -0.079969 -0.365738       1     1.0      752   
15953  0.043682  0.441084 -0.087283 -0.682527       1     1.0      752   
15954  0.052504  0.637302 -0.100934 -1.001363       1     1.0      752   
15955  0.065250  0.833617 -0.120961 -1.323961       1     1.0      752   
15956  0.081922  1.030042 -0.147440 -1.651921       0     1.0      752   
15957  0.102523  0.836918 -0.180479 -1.408568       0     1.0      752   
15958  0.119262  0.644434 -0.208650 -1.177306       0     1.0      752   

       tot_reward  comb_reward  
15947        12.0         12.5  
15948        12.0         12.5  
15949        12.0         12.5  
15950        12.0         12.5  
15951        12.0         12.5  
15952        12.0         12.5  
15953        12.0         12.5  
15954        12.0         12.5  
15955        12.0         12.5  
15956        12.0         12.5  
15957        12.0         12.5  
15958        12.0         12.5

obs0      obs1      obs2      obs3  action  reward  episode  \
15959 -0.004158 -0.005363 -0.002883 -0.035920       0     1.0      753   
15960 -0.004265 -0.200443 -0.003601  0.255852       1     1.0      753   
15961 -0.008274 -0.005270  0.001516 -0.037964       0     1.0      753   
15962 -0.008380 -0.200414  0.000757  0.255196       1     1.0      753   
15963 -0.012388 -0.005302  0.005861 -0.037248       1     1.0      753   
...         ...       ...       ...       ...     ...     ...      ...   
16015 -0.202806 -1.913500  0.035157  1.941495       1     1.0      753   
16016 -0.241076 -1.718771  0.073987  1.659915       0     1.0      753   
16017 -0.275451 -1.914673  0.107186  1.974697       1     1.0      753   
16018 -0.313745 -1.720832  0.146680  1.717056       0     1.0      753   
16019 -0.348161 -1.917300  0.181021  2.051563       0     1.0      753   

       tot_reward  comb_reward  
15959        61.0         61.5  
15960        61.0         61.5  
15961        61.0         61.5  
15962        61.0         61.5  
15963        61.0         61.5  
...           ...          ...  
16015        61.0         61.5  
16016        61.0         61.5  
16017        61.0         61.5  
16018        61.0         61.5  
16019        61.0         61.5  

[61 rows x 9 columns]

obs0      obs1      obs2      obs3  action  reward  episode  \
16020  0.004566  0.027424  0.037558 -0.027077       1     1.0      754   
16021  0.005115  0.221987  0.037016 -0.307678       1     1.0      754   
16022  0.009554  0.416563  0.030862 -0.588461       1     1.0      754   
16023  0.017886  0.611239  0.019093 -0.871264       1     1.0      754   
16024  0.030110  0.806096  0.001668 -1.157884       1     1.0      754   
16025  0.046232  1.001197 -0.021490 -1.450043       0     1.0      754   
16026  0.066256  0.806345 -0.050491 -1.164151       1     1.0      754   
16027  0.082383  1.002087 -0.073774 -1.472227       1     1.0      754   
16028  0.102425  1.198029 -0.103218 -1.787011       0     1.0      754   
16029  0.126385  1.004207 -0.138958 -1.528117       0     1.0      754   
16030  0.146470  0.811008 -0.169521 -1.281834       1     1.0      754   
16031  0.162690  1.007834 -0.195157 -1.622443       0     1.0      754   

       tot_reward  comb_reward  
16020        12.0         12.5  
16021        12.0         12.5  
16022        12.0         12.5  
16023        12.0         12.5  
16024        12.0         12.5  
16025        12.0         12.5  
16026        12.0         12.5  
16027        12.0         12.5  
16028        12.0         12.5  
16029        12.0         12.5  
16030        12.0         12.5  
16031        12.0         12.5

obs0      obs1      obs2      obs3  action  reward  episode  \
16032  0.000105 -0.025437  0.006387 -0.010520       0     1.0      755   
16033 -0.000403 -0.220650  0.006176  0.284171       0     1.0      755   
16034 -0.004816 -0.415860  0.011860  0.578795       0     1.0      755   
16035 -0.013133 -0.611146  0.023436  0.875190       1     1.0      755   
16036 -0.025356 -0.416350  0.040939  0.589967       0     1.0      755   
16037 -0.033683 -0.612021  0.052739  0.895259       1     1.0      755   
16038 -0.045924 -0.417652  0.070644  0.619610       0     1.0      755   
16039 -0.054277 -0.613686  0.083036  0.933679       1     1.0      755   
16040 -0.066551 -0.419776  0.101710  0.668201       1     1.0      755   
16041 -0.074946 -0.226205  0.115074  0.409196       1     1.0      755   
16042 -0.079470 -0.032886  0.123258  0.154893       0     1.0      755   
16043 -0.080128 -0.229538  0.126355  0.483778       1     1.0      755   
16044 -0.084719 -0.036404  0.136031  0.233437       0     1.0      755   
16045 -0.085447 -0.233181  0.140700  0.565746       0     1.0      755   
16046 -0.090110 -0.429967  0.152015  0.899238       0     1.0      755   
16047 -0.098710 -0.626786  0.169999  1.235582       1     1.0      755   
16048 -0.111245 -0.434207  0.194711  1.000617       1     1.0      755   

       tot_reward  comb_reward  
16032        17.0         17.5  
16033        17.0         17.5  
16034        17.0         17.5  
16035        17.0         17.5  
16036        17.0         17.5  
16037        17.0         17.5  
16038        17.0         17.5  
16039        17.0         17.5  
16040        17.0         17.5  
16041        17.0         17.5  
16042        17.0         17.5  
16043        17.0         17.5  
16044        17.0         17.5  
16045        17.0         17.5  
16046        17.0         17.5  
16047        17.0         17.5  
16048        17.0         17.5

In [13]:
memory_df.groupby("episode").reward.sum().mean()

0.014425

# Step 2: Predict

Now that you have a bunch of data, put it into a format that you can model. The goal here is to guide the behavior of our agent. Our agent will be given an observation and need to decide between the possible actions given that observation and the prediction of the model. 

Remember, you're a data scientist! Be creative. 

It might be helpful to work backwards. Ultimately, you will write something like:

```
def convert_to_row(obs, act):
    # expertly written code
    return row_of_obs_act
    
rows = [convert_to_row(current_obs, act) for act in possible_actions]

pred_outcome = model.predict(rows)
```

So, you will need to design a quantity that you can ask your model to predict for every possible action-observation pair. Think a bit about what this quantity should be. Should the model try to predict the immediate reward for each action? If so, how would it know where to go at the beginning of each episode when all moves give zero reward but when some moves bring it closer to the goal than others. 

In [14]:
from sklearn.ensemble import RandomForestRegressor, ExtraTreesRegressor
from sklearn.svm import SVR

model = ExtraTreesRegressor(n_estimators=50)
# model = SVR()
y = 0.5*memory_df.reward + 0.1*memory_df.decay_reward + memory_df.tot_reward
x = memory_df[["observation", "action"]]
model.fit(x, y)

ExtraTreesRegressor(n_estimators=50)

# Step 3: Act

Now that you have a model that predicts the desired behavior, let's act on it! Modify the code you used to gather data so that you replace the random decision with an intelligent one.

We started out winning ~1.5% of the games with the random agent. How well can you do? You should be able to get your model to do at least 10x better (so 15%). Can you get ~50%?

If you're having trouble, tune your model. Try different representations of the observation and action spaces. Try different models. 

In [15]:
model = RandomForestRegressor()
y = 1*memory_df.reward + memory_df.tot_reward + .1*memory_df.decay_reward
x = memory_df[["observation", "action"]]
model.fit(x, y)

num_episodes = 500
random_per = 0

life_memory = []
for i in range(num_episodes):
    
    # start a new episode and record all the memories
    old_observation = env.reset()
    done = False
    tot_reward = 0
    ep_memory = []
    while not done:
        
        
        if np.random.rand() < random_per:
            new_action = env.action_space.sample()
        else:
            pred_in = [[old_observation,i] for i in range(4)]
            new_action = np.argmax(model.predict(pred_in))
        observation, reward, done, info = env.step(new_action)
        tot_reward += reward
        
        ep_memory.append({
            "observation": old_observation,
            "action": new_action,
            "reward": reward,
            "episode": i,
        })
        old_observation = observation
        
    # incorporate total reward
    for ep_mem in ep_memory:
        ep_mem["tot_reward"] = tot_reward
        
    life_memory.extend(ep_memory)
    
memory_df2 = pandas.DataFrame(life_memory)

# rf.fit(memory_df[["observation", "action"]], memory_df["comb_reward"])

# score
# much better!
memory_df2.groupby("episode").reward.sum().mean()

0.71

In [16]:
y = .1*memory_df.reward + 1*memory_df.decay_reward + 1*memory_df.tot_reward

# Extension: Pole cart

If time permits, try your hand at pole cart (`env = gym.make('CartPole-v0')`).

Notice that the observation space is quite different. It's no longer discrete--instead we have 4 continuous values. You'll have to store these differently from how you did with Frozenlake.

My random actor actually does surprisingly well (avg ~22). But my intelligent agent is able to score ~99. Can you beat me? 

# Pole cart

In [17]:
env = gym.make('CartPole-v0')

In [18]:
# now we can build a toy world!
num_episodes = 1000

life_memory = []
for i in range(num_episodes):
    
    # start a new episode and record all the memories
    old_observation = env.reset()
    done = False
    tot_reward = 0
    ep_memory = []
    while not done:
        new_action = env.action_space.sample()
        observation, reward, done, info = env.step(new_action)
        tot_reward += reward
        
        ep_memory.append({
            "obs0": old_observation[0],
            "obs1": old_observation[1],
            "obs2": old_observation[2],
            "obs3": old_observation[3],
            "action": new_action,
            "reward": reward,
            "episode": i,
        })
        old_observation = observation
        
    # incorporate total reward
    for ep_mem in ep_memory:
        ep_mem["tot_reward"] = tot_reward
        
    life_memory.extend(ep_memory)
    
memory_df = pandas.DataFrame(life_memory)

memory_df.groupby("episode").reward.sum().mean()

21.297

In [19]:
memory_df.describe()

obs0          obs1          obs2          obs3        action  \
count  21297.000000  21297.000000  21297.000000  21297.000000  21297.000000   
mean       0.003421      0.017633      0.000610     -0.010889      0.504625   
std        0.082175      0.534333      0.091749      0.798357      0.499990   
min       -0.595480     -2.292106     -0.209390     -2.842624      0.000000   
25%       -0.039220     -0.351284     -0.052411     -0.535880      0.000000   
50%        0.001050      0.004174      0.002194     -0.003267      1.000000   
75%        0.041845      0.373108      0.054208      0.522124      1.000000   
max        0.846484      2.515854      0.209439      2.837651      1.000000   

        reward       episode    tot_reward  
count  21297.0  21297.000000  21297.000000  
mean       1.0    498.743955     26.905527  
std        0.0    288.790000     13.764576  
min        1.0      0.000000      8.000000  
25%        1.0    246.000000     16.000000  
50%        1.0    498.000000     23.000000  
75%        1.0    753.000000     34.000000  
max        1.0    999.000000     72.000000

In [20]:
from sklearn.ensemble import RandomForestRegressor, AdaBoostRegressor, ExtraTreesRegressor

model = ExtraTreesRegressor(n_estimators=50)

memory_df["comb_reward"] = .5*memory_df.reward + memory_df.tot_reward
model.fit(memory_df[["obs0", "obs1", "obs2", "obs3", "action"]], memory_df.comb_reward)

ExtraTreesRegressor(n_estimators=50)

In [21]:
num_episodes = 100
random_per = 0

life_memory = []
for i in range(num_episodes):
    
    # start a new episode and record all the memories
    old_observation = env.reset()
    done = False
    tot_reward = 0
    ep_memory = []
    while not done:
        
        
        if np.random.rand() < random_per:
            new_action = env.action_space.sample()
        else:
            pred_in = [list(old_observation)+[i] for i in range(2)]
            new_action = np.argmax(model.predict(pred_in))
        observation, reward, done, info = env.step(new_action)
        tot_reward += reward
        
        ep_memory.append({
            "obs0": old_observation[0],
            "obs1": old_observation[1],
            "obs2": old_observation[2],
            "obs3": old_observation[3],
            "action": new_action,
            "reward": reward,
            "episode": i,
        })
        old_observation = observation
        
    # incorporate total reward
    for ep_mem in ep_memory:
        ep_mem["tot_reward"] = tot_reward
        
    life_memory.extend(ep_memory)
    
memory_df2 = pandas.DataFrame(life_memory)
memory_df2["comb_reward"] = memory_df2.reward + memory_df2.tot_reward

# score
# much better!
memory_df2.groupby("episode").reward.sum().mean()

88.84

---
### Machine Learning Foundation (C) 2020 IBM Corporation